In [1]:
import os
# set the current working directory. This is required by isaac.
# This cell should only run once.
os.chdir("../../../")
os.getcwd()

'/home/mrobotics2/.cache/bazel/_bazel_mrobotics2/36d61b35046788db1f2a67ff239dff81/execroot/com_nvidia_isaac_sdk/bazel-out/k8-opt/bin/apps/samples/manipulation/simple_joint_control.runfiles/com_nvidia_isaac_sdk'

In [2]:
from IPython.display import display
import json
import numpy as np

from packages.pyalice import Application, Codelet,Message, Composite
from packages.pyalice.gui.composite_widget import CompositeWidget

np.set_printoptions(precision=3)

# Sophia Left Arm Simulator using Composite Widget
---




Sophia Kinematic file import and get the joint,
Example - ['13','17','19','21']

In [3]:
# set kinematic file and get list of joints for sophia
kinematic_file = "/home/mrobotics2/Desktop/isaac/sdk/apps/assets/kinematic_trees/sophia.kinematic.json"
# kinematic_file = "/home/mrobotics2/Desktop/isaac/sdk/apps/assets/kinematic_trees/one_motor.kinematic.json"
joints = []
with open(kinematic_file,'r') as fd:
    kt = json.load(fd)
    for link in kt['links']:
        if 'motor' in link and link['motor']['type'] != 'constant':
            joints.append(link['name'])
print(joints)

['13', '17', '19', '21']



1. Replace Simlation with Driver, whatever is sent to and from simulation is to be done by driver.
2. 

In [4]:
# A Python codelet for joint control through widget
# def even_list():
#     odd_i = [] 
#     even_i = [] 
#     for i in range(0, len(test_list)): 
#         if i % 2: 
#             even_i.append(test_list[i]) 
#         else : 
#             odd_i.append(test_list[i]) 
#     return even_i

class DriverInputControl(Codelet):
    def start(self):
        self.rx = self.isaac_proto_rx("CompositeProto", "command")
        self.tx = self.isaac_proto_tx("StateProto", "state")
        self.tick_periodically(0.2)

    def tick(self):
        state_msg = self.rx.message
        if state_msg is None:
            return "Received None in DriverInputControl"
        
        # Get the Value of tensor and send value further, Supposed to get values for 4 joints
        # Hence a total of 8 values in a tensor list.
        angles_list_dynamixel = state_msg.tensor
        print('Checking Size of tensor ')
#         tensor_size = len(state_msg.tensor)
#         if(tensor_size == 8):
#             print('Size of Tensor Received from Composite is ', state_msg.tensor, ' and its size if  ', len(state_msg.tensor))
#             angles_list = even_list(state_msg.tensor)
#             angles_list_dynamixel = [int(i * 651.8986) for i in angles_list]
#         elif tensor_size == 4:
#             angles_list_dynamixel = [int(i * 651.8986) for i in state_msg.tensor]
#         if len(angles_list_dynamixel) > 4: print("List Value for Dynamixel Exceeds 4")
#         print('Checking List of size 4')
#         angles_list_dynamixel = [int(i * 651.8986) for i in state_msg.tensor]
        print('Message Received from Composite Proto', state_msg.tensor)
        #Convert List
        
        
        tx_message = self.tx.init()
        
        #Adding to Proto
        tx_message.proto.pack.elementType = 3  # Float64
        tx_message.proto.pack.sizes = [1, 1, 4]
        tx_message.proto.pack.scanlineStride = 0
        tx_message.proto.pack.dataBufferIndex = 0
        tx_message.proto.schema = "StateProto"
        
        print('Sophia Left Arm Mode')
        buffer = np.empty([1, 1, 4], dtype=np.dtype('float64'))
        buffer[0][0][0] = angles_list_dynamixel[0]     # 13  - [750-3480]
        buffer[0][0][1] = angles_list_dynamixel[1]      # 17  - [198-3859]
        buffer[0][0][2] = angles_list_dynamixel[2]      # 19  - [1643-2297]
        buffer[0][0][3] = angles_list_dynamixel[3]      # 21  - [1783-2383]
        
#         buffer[0][0][0] =        # 13  - [750-3480]
#         buffer[0][0][1] = 1500      # 17  - [198-3859]
#         buffer[0][0][2] = 2100      # 19  - [1643-2297]
#         buffer[0][0][3] = 1800      # 21  - [1783-2383]
        
        '''
          Set Buffer
        '''
        tx_message.buffers = [buffer]
        self.tx.publish()

In [5]:
# A Python codelet for joint control through widget
import numpy as np
class DriverOutputControl(Codelet):
    def start(self):
        self.rx = self.isaac_proto_rx("StateProto", "command")
        self.tx = self.isaac_proto_tx("CompositeProto", "state")
#         self._widget = CompositeWidget(self.config.joints, self.config.measure, self.config.limits)
        self.tick_periodically(1)
        print("Inside START of Driver OUTPUT")

    def tick(self):
        print('Inside TICK Sophia Output')
        state_msg = self.rx.message  # MessageReader
        if state_msg is None:
            print('______________________________________________________________________________')
            return "Nothing Received"
        if(False):
            print('\t__Message received with following Detials__')
            print('State Proto Pack  {}'.format(state_msg.proto.pack))
            print('Schema {}'.format(state_msg.proto.schema))
            print('Data {}'.format(state_msg.proto.data))
            print("Tensor  {}".format(state_msg.tensor))
            print('\t__END__')
            
        # Making Composite Message
        '''
        '''
        measure = "position"
        quantities = [[x, measure, 1] for x in joints]
#         print('Quantities are : \n', quantities)
        
#         print('Tensor Value from State Proto of ARM is ', state_msg.tensor[0][0],' and type  : ',type(state_msg.tensor))
        values = state_msg.tensor[0][0] #Send entire array
        
        comp_msg = Composite.create_composite_message(quantities, values)
#         print('Proto of  Message is : ',comp_msg.proto)
#         print('Tensor of Message :: ', comp_msg.proto.tensor)
        
        
        #Send Message out
        tx_message = self.tx.init()
        
        tx_message.proto = comp_msg.proto
        tx_message.buffers = comp_msg.buffers
        
        self.tx.publish()
        
        
        

In [6]:
# A Python codelet for joint control through widget
class JointControl(Codelet):
    def start(self):
        print('\n --Inside Joint Controller-- \n')
        self.rx = self.isaac_proto_rx("CompositeProto", "command")
        self.tx = self.isaac_proto_tx("CompositeProto", "state")
        print('------------------------------  Step IN   ')
        self._widget = CompositeWidget(self.config.joints, self.config.measure, self.config.limits)
        print('------------------------------  Step OUT  ')
        if self._widget is None:
            report_failure("Cannot create valid widget")
            return "Cannot Create Valid Widget"
        display(self._widget.panel)
        self.tick_periodically(0.1)

    def tick(self):
        state_msg = self.rx.message
        
        if state_msg is None:
            return "NOTHING IS BEING RECEIVED BY DRIVER SOPHIA OUTPUT"
        
        print('Length of Quantities',len(state_msg.proto.quantities))
        print('Length of Tensor : ',len(state_msg.tensor))
        print('Quantities of ')
        self._widget.composite = state_msg
        
        self.tx._msg = self._widget.composite
        if self.tx._msg is not None:
            self.tx.publish()


In [7]:
'''
MAIN APPLICATION
'''


app = Application(name="simple_joint_control_lqr_sophia_larm")

# Load Applications
app.load(filename="/home/mrobotics2/Desktop/isaac/sdk/packages/planner/apps/multi_joint_lqr_control.subgraph.json", prefix="lqr")
lqr_interface = app.nodes["lqr.subgraph"]["interface"]

# # LQR configs
app.nodes["lqr.kinematic_tree"]["KinematicTree"].config.kinematic_file = kinematic_file
lqr_planner = app.nodes["lqr.local_plan"]["MultiJointLqrPlanner"]
lqr_planner.config.speed_min = [-1.0] * len(joints)
lqr_planner.config.speed_max = [1.0] * len(joints)
lqr_planner.config.acceleration_min = [-1.0] * len(joints)
lqr_planner.config.acceleration_max = [1.0] * len(joints)



# add pycodelet JointControl for arm control
joint_commander = app.add("command_generator").add(JointControl)
joint_commander.config.joints = joints
joint_commander.config.limits = [[750,3480],[198,3859],[1643,2297],[1783,2383]]
joint_commander.config.measure = "position"


#Adding nodes to Application
driver_sophia_output =  app.nodes["lqr.driver_sophia_output"]["DriverOutputControl"]
driver_sophia_input =  app.nodes["lqr.driver_sophia_input"]["DriverInputControl"]

app.nodes["lqr.driver_sophia_input"].add(name="DriverInputControl", ctype=DriverInputControl)
app.nodes["lqr.driver_sophia_output"].add(name="DriverOutputControl", ctype=DriverOutputControl)


# Edges
app.connect(driver_sophia_output, "state", joint_commander, "command")  # driver_output ----> joint_commander
app.connect(joint_commander, "state", driver_sophia_input, "command")  # driver_output ----> joint_commander



app.start()
#Make Dynamixel Work

2021-02-25 17:14:56,069 DEBUG Binding PyCodelet command_generator/PyCodelet
2021-02-25 17:14:56,070 DEBUG Binding PyCodelet lqr.driver_sophia_input/DriverInputControl
2021-02-25 17:14:56,071 DEBUG Binding PyCodelet lqr.driver_sophia_output/DriverOutputControl
2021-02-25 17:14:56,072 DEBUG Launching isaac core
2021-02-25 17:14:56,073 DEBUG Launching pycodelet threads
2021-02-25 17:14:56,074 DEBUG Launching command_generator/PyCodelet
2021-02-25 17:14:56,075 DEBUG Launching lqr.driver_sophia_input/DriverInputControl
2021-02-25 17:14:56,075 DEBUG Launching lqr.driver_sophia_output/DriverOutputControl



 --Inside Joint Controller-- 

------------------------------  Step IN   
------------------------------  Step OUT  


Inside START of Driver OUTPUT
Inside TICK Sophia Output
______________________________________________________________________________
Inside TICK Sophia Output
Length of Quantities 4
Length of Tensor :  4
Quantities of 
LOGDEBUG  ---------- Length/Count of quantities 4
LOGDEBUG ---------- Priniting entire message.json : {'quantities': [{'entity': '13', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '17', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '21', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}], 'schemaHash': '', 'values': {'elementType': 'float64', 'sizes': [4], 'scanlineStride': 0, 'dataBufferIndex': 0}}
LOGDEBUG  ----------  d is  1
LOGDEBUG  ---------- PRINTING ENTIRE QUANTITIES :  [['13', 'position', 1], ['17', 'position', 1], ['1

Length of Quantities 4
Length of Tensor :  4
Quantities of 
LOGDEBUG  ---------- Length/Count of quantities 4
LOGDEBUG ---------- Priniting entire message.json : {'quantities': [{'entity': '13', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '17', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '21', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}], 'schemaHash': '', 'values': {'elementType': 'float64', 'sizes': [4], 'scanlineStride': 0, 'dataBufferIndex': 0}}
LOGDEBUG  ----------  d is  1
LOGDEBUG  ---------- PRINTING ENTIRE QUANTITIES :  [['13', 'position', 1], ['17', 'position', 1], ['19', 'position', 1], ['21', 'position', 1]]
LOGDEBUG ---------- Printing p and q : ['13', 'position', 1] and {'entity': '13', 'elementType': 'float64', 'measure':

LOGDEBUG  ----------  d is  1
LOGDEBUG  ---------- PRINTING ENTIRE QUANTITIES :  [['13', 'position', 1], ['17', 'position', 1], ['19', 'position', 1], ['21', 'position', 1]]
LOGDEBUG ---------- Printing p and q : ['13', 'position', 1] and {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}} 
LOGDEBUG ---------- Printing p and q : ['17', 'position', 1] and {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}} 
LOGDEBUG ---------- Printing p and q : ['19', 'position', 1] and {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}} 
LOGDEBUG ---------- Printing p and q : ['21', 'position', 1] and {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}} 
LOGDEBUG  ----------  d is  1
LOGDEBUG  ---------- PRINTING ENTIRE QUANTITIES :  [['13', 'position', 1], ['17', 'position', 1], ['19', 'position', 1],

...

Checking Size of tensor 
Message Received from Composite Proto [1577.37  1398.475 2073.087 1846.538]
Sophia Left Arm Mode
Inside TICK Sophia Output
Length of Quantities 4
Length of Tensor :  4
Quantities of 
LOGDEBUG  ---------- Length/Count of quantities 4
LOGDEBUG ---------- Priniting entire message.json : {'quantities': [{'entity': '13', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '17', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '21', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}], 'schemaHash': '', 'values': {'elementType': 'float64', 'sizes': [4], 'scanlineStride': 0, 'dataBufferIndex': 0}}
LOGDEBUG  ----------  d is  1
LOGDEBUG  ---------- PRINTING ENTIRE QUANTITIES :  [['13', 'position', 1], ['17', 'position', 1], ['19', 'position

Sophia Left Arm Mode
Length of Quantities 4
Length of Tensor :  4
Quantities of 
LOGDEBUG  ---------- Length/Count of quantities 4
LOGDEBUG ---------- Priniting entire message.json : {'quantities': [{'entity': '13', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '17', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '21', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}], 'schemaHash': '', 'values': {'elementType': 'float64', 'sizes': [4], 'scanlineStride': 0, 'dataBufferIndex': 0}}
LOGDEBUG  ----------  d is  1
LOGDEBUG  ---------- PRINTING ENTIRE QUANTITIES :  [['13', 'position', 1], ['17', 'position', 1], ['19', 'position', 1], ['21', 'position', 1]]
LOGDEBUG ---------- Printing p and q : ['13', 'position', 1] and {'entity': '13', 'elementType': 

Length of Quantities 4
Length of Tensor :  4
Quantities of 
LOGDEBUG  ---------- Length/Count of quantities 4
LOGDEBUG ---------- Priniting entire message.json : {'quantities': [{'entity': '13', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '17', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '21', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}], 'schemaHash': '', 'values': {'elementType': 'float64', 'sizes': [4], 'scanlineStride': 0, 'dataBufferIndex': 0}}
LOGDEBUG  ----------  d is  1
LOGDEBUG  ---------- PRINTING ENTIRE QUANTITIES :  [['13', 'position', 1], ['17', 'position', 1], ['19', 'position', 1], ['21', 'position', 1]]
LOGDEBUG ---------- Printing p and q : ['13', 'position', 1] and {'entity': '13', 'elementType': 'float64', 'measure':

Length of Quantities 4
Length of Tensor :  4
Quantities of 
LOGDEBUG  ---------- Length/Count of quantities 4
LOGDEBUG ---------- Priniting entire message.json : {'quantities': [{'entity': '13', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '17', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '21', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}], 'schemaHash': '', 'values': {'elementType': 'float64', 'sizes': [4], 'scanlineStride': 0, 'dataBufferIndex': 0}}
LOGDEBUG  ----------  d is  1
LOGDEBUG  ---------- PRINTING ENTIRE QUANTITIES :  [['13', 'position', 1], ['17', 'position', 1], ['19', 'position', 1], ['21', 'position', 1]]
LOGDEBUG ---------- Printing p and q : ['13', 'position', 1] and {'entity': '13', 'elementType': 'float64', 'measure':

Checking Size of tensor 
Message Received from Composite Proto [1577.37  1398.475 2073.087 1846.538]
Sophia Left Arm Mode
Inside TICK Sophia Output
Length of Quantities 4
Length of Tensor :  4
Quantities of 
LOGDEBUG  ---------- Length/Count of quantities 4
LOGDEBUG ---------- Priniting entire message.json : {'quantities': [{'entity': '13', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '17', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '19', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}, {'entity': '21', 'elementType': 'float64', 'measure': 'position', 'dimensions': {'coefficients': [1]}}], 'schemaHash': '', 'values': {'elementType': 'float64', 'sizes': [4], 'scanlineStride': 0, 'dataBufferIndex': 0}}
LOGDEBUG  ----------  d is  1
LOGDEBUG  ---------- PRINTING ENTIRE QUANTITIES :  [['13', 'position', 1], ['17', 'position', 1], ['19', 'position

In [ ]:
app.stop()

In [ ]:
# app = Application(name="simple_joint_control_lqr_sophia_larm")

# # Load Applications
# app.load(filename="/home/mrobotics2/Desktop/isaac/sdk/packages/planner/apps/multi_joint_lqr_control.subgraph.json", prefix="lqr")
# lqr_interface = app.nodes["lqr.subgraph"]["interface"]

# #Dynamixel Interface
# # dynamixel_driver = app.nodes["lqr.dynamixel"]["driver"]

# #Driver Nodes - Sophia Larm
# # driver_sophia_input =  app.nodes["lqr.driver_sophia_input"]["DriverInputControl"]
# driver_sophia_output =  app.nodes["lqr.driver_sophia_output"]["DriverOutputControl"]


# # driver -> lqr
# #lqr -> driver
# # app.connect(driver_sophia_output, "state", lqr_interface, "joint_command")
# # app.connect(lqr_interface, "joint_state", driver_sophia_input, "command")


# # LQR configs
# app.nodes["lqr.kinematic_tree"]["KinematicTree"].config.kinematic_file = kinematic_file
# lqr_planner = app.nodes["lqr.local_plan"]["MultiJointLqrPlanner"]
# lqr_planner.config.speed_min = [-1.0] * len(joints)
# lqr_planner.config.speed_max = [1.0] * len(joints)
# lqr_planner.config.acceleration_min = [-1.0] * len(joints)
# lqr_planner.config.acceleration_max = [1.0] * len(joints)

# #Edges for Driver and Config
# # app.connect(driver_sophia_input, "state", dynamixel_driver, "command") # sophia_input ----> dynamixel_driver
# # app.connect(dynamixel_driver, "state", driver_sophia_output, "command") # dynamixel-driver -----> sophia_outptu
# # driver_sophia_output.config.joints = joints
# # driver_sophia_output.config.measure = "position"

# # add pycodelet JointControl for arm control
# joint_commander = app.add("command_generator").add(JointControl)
# joint_commander.config.joints = joints
# joint_commander.config.limits = [[0.2791845034, 4.4],[0.32, 5.95],[3.003534383, 3.882505374],[3.103243134, 4.017495683]]
# joint_commander.config.measure = "position"
# #Edges
# app.connect(joint_commander, "command", lqr_interface, "joint_target") #jointcommander ---> lqr
# app.connect(driver_sophia_output, "command", joint_commander, "state")  # driver_output ----> joint_commander


# app.nodes["command_generator"].add(name="JointControl", ctype=JointControl)
# app.nodes["lqr.driver_sopjoint_commandhia_input"].add(name="DriverInputControl", ctype=DriverInputControl)
# app.nodes["lqr.driver_sophia_output"].add(name="DriverOutputControl", ctype=DriverOutputControl)


# app.start()

UR10 with LQR planner in Omniverse Isaac Sim
======

Open the ur10_playground stage in Kit, start Robot Engine Bridge and hit Play before continuing

In [ ]:
# set kinematic file and get list of joints
kinematic_file = "apps/assets/kinematic_trees/ur10.kinematic.json"
joints = []
with open(kinematic_file,'r') as fd:
    kt = json.load(fd)
    for link in kt['links']:
        if 'motor' in link and link['motor']['type'] != 'constant':
            joints.append(link['name'])
print(joints)

In [ ]:
app = Application(name="simple_joint_control_lqr_ur10_sim")

# load subgraphs
app.load(filename="packages/planner/apps/multi_joint_lqr_control.subgraph.json", prefix="lqr")
app.load(filename="packages/navsim/apps/navsim_tcp.subgraph.json", prefix="simulation")
# edges
simulation_node = app.nodes["simulation.interface"]
lqr_interface = app.nodes["lqr.subgraph"]["interface"]
app.connect(simulation_node["output"], "joint_state", lqr_interface, "joint_state")
app.connect(lqr_interface, "joint_command", simulation_node["input"], "joint_position")

# configs
app.nodes["lqr.kinematic_tree"]["KinematicTree"].config.kinematic_file = kinematic_file
lqr_planner = app.nodes["lqr.local_plan"]["MultiJointLqrPlanner"]
lqr_planner.config.speed_min = [-1.0] * len(joints)
lqr_planner.config.speed_max = [1.0] * len(joints)
lqr_planner.config.acceleration_min = [-1.0] * len(joints)
lqr_planner.config.acceleration_max = [1.0] * len(joints)

# add pycodelet JointControl for arm control
joint_commander = app.add("command_generator").add(JointControl)
joint_commander.config.joints = joints
joint_commander.config.limits = [[-2*np.pi, 2*np.pi]] * len(joints)
joint_commander.config.measure = "position"
app.connect(joint_commander, "command", lqr_interface, "joint_target")
app.connect(simulation_node["output"], "joint_state", joint_commander, "state")

# add pycodelet JointPreview as a preview node between simulation and JointControl
# joint_preview = app.add("command_preview").add(JointPreview)
# joint_commander.config.joints = joints
# joint_commander.config.limits = [[-2*np.pi, 2*np.pi]] * len(joints)
# joint_commander.config.measure = "position"
# app.connect(joint_commander, "command", lqr_interface, "joint_target")
# app.connect(simulation_node["output"], "joint_state", joint_commander, "state")

# add pycodelet JointControl for finger control
finger_commander = app.add("finger_generator").add(JointControl)
finger_commander.config.joints = ["gripper"]
finger_commander.config.limits = [[0.0, 1.0]] * len(finger_commander.config.joints)
finger_commander.config.measure = "none"
app.connect(finger_commander, "command", simulation_node["input"], "io_command")
app.connect(simulation_node["output"], "io_state", finger_commander, "state")

app.start()

In [ ]:
# stop Isaac app
app.stop()

UR10 with RMP planner in Omniverse Isaac Sim
======

Open the ur10_playground stage in Kit, start Robot Engine Bridge and hit Play before continuing

In [ ]:
# set kinematic file and get list of joints
kinematic_file = "apps/assets/kinematic_trees/ur10.kinematic.json"
joints = []
with open(kinematic_file,'r') as fd:
    kt = json.load(fd)
    for link in kt['links']:
        if 'motor' in link and link['motor']['type'] != 'constant':
            joints.append(link['name'])
print(joints)

In [ ]:
app = Application(name="simple_joint_control_rmp_ur10_sim")

# load subgraphs
app.load(filename="packages/planner/apps/multi_joint_rmp_control.subgraph.json", prefix="rmp")
app.load(filename="packages/navsim/apps/navsim_tcp.subgraph.json", prefix="simulation")
# edges
simulation_node = app.nodes["simulation.interface"]
rmp_interface = app.nodes["rmp.subgraph"]["interface"]
app.connect(simulation_node["output"], "joint_state", rmp_interface, "joint_state")
app.connect(rmp_interface, "joint_command", simulation_node["input"], "joint_position")
# configs
app.nodes["rmp.kinematic_tree"]["KinematicTree"].config.kinematic_file = kinematic_file
rmp_planner = app.nodes["rmp.local_plan"]["MultiJointRmpPlanner"]
rmp_planner.config.rmpflow_config_file = "apps/assets/lula_assets/ur10_rmpflow_config.yaml"
rmp_planner.config.robot_description_file = "apps/assets/lula_assets/ur10_robot_description.yaml"
rmp_planner.config.robot_urdf = "apps/assets/lula_assets/ur10_robot.urdf"
rmp_planner.config.end_effector_frame = "tool"

# add pycodelet JointPositionControl
widget_node = app.add("command_generator")
joint_commander = widget_node.add(JointControl)
joint_commander.config.joints = joints
joint_commander.config.limits = [[-2*np.pi, 2*np.pi]] * len(joints)
joint_commander.config.measure = "position"
app.connect(joint_commander, "command", rmp_interface, "joint_target")
app.connect(simulation_node["output"], "joint_state", joint_commander, "state")
                            
app.start()

In [ ]:
# stop Isaac app
app.stop()

Kinova Jaco (gen2, 7 joints) Hardware
======

Install the KinoveJaco SDK in /opt/JACO2SDK (tested with v1.4.2) and connect to workstation via USB. Make sure the USB port has write permission

In [ ]:
kinematic_file = "apps/assets/kinematic_trees/kinova.kinematic.json"
joints = []
with open(kinematic_file,'r') as fd:
    kt = json.load(fd)
    for link in kt['links']:
        if 'motor' in link and link['motor']['type'] != 'constant':
            joints.append(link['name'])
print(joints)

In [ ]:
app = Application(name="simple_joint_control_kinova_real")

# load lqr subgraphcs
app.load(filename="packages/planner/apps/multi_joint_lqr_control.subgraph.json", prefix="lqr")
lqr_interface = app.nodes["lqr.subgraph"]["interface"]
# add kinova driver codelet
app.load_module("kinova_jaco")
- = app.add("driver").add(app.registry.isaac.kinova_jaco.KinovaJaco)
# edges
app.connect(driver, "arm_state", lqr_interface, "joint_state")
app.connect(lqr_interface, "joint_command", driver, "arm_command")
# configs
app.nodes["lqr.kinematic_tree"]["KinematicTree"].config.kinematic_file = kinematic_file
lqr_planner = app.nodes["lqr.local_plan"]["MultiJointLqrPlanner"]
lqr_planner.config.speed_min = [-0.5] * len(joints)
lqr_planner.config.speed_max = [0.5] * len(joints)
lqr_planner.config.acceleration_min = [-0.5] * len(joints)
lqr_planner.config.acceleration_max = [0.5] * len(joints)
app.nodes["lqr.controller"]["MultiJointController"].config.control_mode = "speed"
driver.config.kinematic_tree = "lqr.kinematic_tree"
driver.config.kinova_jaco_sdk_path = "/opt/JACO2SDK/API/"
driver.config.tick_period = "10ms"
driver.config.control_mode = "joint velocity"

# add pycodelet JointControl for arm control
joint_commander = app.add("command_generator").add(JointControl)
joint_commander.config.joints = joints
joint_commander.config.limits = [[-2*np.pi, 2*np.pi]] * len(joints)
joint_commander.config.measure = "position"
app.connect(joint_commander, "command", lqr_interface, "joint_target")
app.connect(driver, "arm_state", joint_commander, "state")

# add pycodelet JointControl for finger control
finger_commander = app.add("finger_generator").add(JointControl)
finger_commander.config.joints = ["finger1", "finger2", "finger3"]
finger_commander.config.limits = [[0.0, 1.0]] * len(finger_commander.config.joints)
finger_commander.config.measure = "none"

app.connect(finger_commander, "command", driver, "finger_command")
app.connect(driver, "finger_state", finger_commander, "state")

app.start()

In [ ]:
app.stop()